<a href="https://colab.research.google.com/github/WEKSTER08/Video_Super_resolution/blob/main/Untitled1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install git+https://github.com/huggingface/diffusers.git
!pip install accelerate

import cv2
import torch
from torchvision.models import vgg19
from torchvision.transforms import ToTensor
import requests
from PIL import Image
from io import BytesIO
from diffusers import LDMSuperResolutionPipeline

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Cloning https://github.com/huggingface/diffusers.git to /tmp/pip-req-build-l4h18ybm
  Running command git clone --filter=blob:none --quiet https://github.com/huggingface/diffusers.git /tmp/pip-req-build-l4h18ybm
  Resolved https://github.com/huggingface/diffusers.git to commit 5559d0423771e8b6e454b1541164e0d5d54b6265
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 224.5/224.5 kB 9.6 MB/s eta 0:00:00
  Created wheel for diffusers: filename=diffusers-0.17.0.dev0-py3-none-any.whl size=1071480 sha256=6a1bfe17e6c143f7d5be7c695e1ebc6c41f9ef4a750ab4274ca64c2c67bcf6bd
  Stored in directory: /tmp/pip-ephem-wheel-cache-pgc3eyts/wheels/4d/b7/a8/6f9549ceec5daad78675b857ac57d697c387062506520a7b50
Successfully built diffusers
Looking in indexes: https://pypi.org/simple, 

In [2]:
# Load the Drive helper and mount
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [6]:
%cd drive/MyDrive

/content/drive/MyDrive


'06_Tutorial(Sept2-6)_solutions.pdf'
'07_Tutorial(Sept9-14)_solutions.pdf'
'08_Tutorial(Sept16-20)_Solutions.pdf'
 09_science_sa2_solved_01_new.pdf
 09_science_sa2_solved_01_new_sol_kde.pdf
 09_science_sa2_solved_02_new.pdf
 09_science_sa2_solved_02_new_sol_dge.pdf
 09_science_sa2_solved_03_new.pdf
 09_science_sa2_solved_03_new_sol_isk.pdf
 09_science_sa2_solved_04_new.pdf
 09_science_sa2_solved_04_new_sol_evs.pdf
 09_science_sa2_solved_05_new.pdf
 09_science_sa2_solved_05_new_sol_sge.pdf
'09_Tutorial(Sept23-27)_solutions (1).pdf'
'09_Tutorial(Sept23-27)_solutions.pdf'
 11-Grade_3_Maths_Assessment.docx
 12-A1.pdf
'1-2 sem REGULAR (19-BATCH).docx'
'14_Tutorial(Nov11-15)_solutions.pdf'
'15_Tutorial(Nov18-22)_Solutions.pdf'
'19512_DLD&CA_1-3-21.pdf'
'19512_DLD&CA_3-3-2021.pdf'
'19512_DLD&CA_3-3-21.pdf'
 19512_DLDCA_9-4-21.pdf
'19512--Graphic Novel.gdoc'
 19512_Sriyugesh_La4.zip
 19512_Sriyugesh_Lab2.zip
'19512 tut6solns.pdf'
 19XJ1A0512--Advertisement.gdoc
 19XJ1A0512.pdf
 19XJ1A0512_Sriy

In [ ]:
import cv2
import torch
from torchvision.models import vgg19
from torchvision.transforms import ToTensor
import numpy as np
from multiprocessing import Process
import torch.multiprocessing as mp


# Set device to use GPU if available, otherwise use CPU
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

# Load the ESRGAN model
# model = torch.load('path_to_esrgan_model.pth').to(device)

# Set up VGG19 network for feature extraction
vgg = vgg19(pretrained=True).features[:35].to(device)
for param in vgg.parameters():
    param.requires_grad = False

# Define the ESRGAN function
def esrgan(low_res_img):
    model_id = "CompVis/ldm-super-resolution-4x-openimages"

    # load model and scheduler
    pipeline = LDMSuperResolutionPipeline.from_pretrained(model_id)
    pipeline = pipeline.to(device)

    # let's download an  image
    
    # low_res_img = low_res_img.resize((128, 128))
    image = ToTensor()(low_res_img).unsqueeze(0).to(device)
    # run pipeline in inference (sample random noise and denoise)
    # low_res_img = torch.from_numpy(low_res_img).long()
    upscaled_image = pipeline(image, num_inference_steps=5, eta=1).images[0]
    return upscaled_image

# Define the function to process a video
def upscale_video(input_path, output_path):
    # Open the video file
    video = cv2.VideoCapture(input_path)

    # Get video properties
    width = int(video.get(cv2.CAP_PROP_FRAME_WIDTH))
    height = int(video.get(cv2.CAP_PROP_FRAME_HEIGHT))
    fps = video.get(cv2.CAP_PROP_FPS)
    total_frames = int(video.get(cv2.CAP_PROP_FRAME_COUNT))

    # Create output video writer
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = cv2.VideoWriter(output_path, fourcc, fps, (width, height))

    frame_count = 0
    while True:
        # Read the next frame
        ret, frame = video.read()
        if not ret:
            break

        # Upscale the frame using ESRGAN
        enhanced_frame = esrgan(frame)

        # Convert tensor to numpy array
        enhanced_frame = np.array(enhanced_frame)
        enhanced_frame = np.clip(enhanced_frame, 0, 255).astype(np.uint8)
        # Write the enhanced frame to the output video
        out.write(enhanced_frame)

        frame_count += 1
        print(f'Processing frame {frame_count}/{total_frames}')

    # Release resources
    video.release()
    out.release()

    print('Video upscaling complete!')


# Usage example
input_video_path = 'Birthday_with_papa.mp4'
output_video_path = 'Output.mp4'

# mp.set_start_method('spawn',force=True)
# p = mp.Process(target=upscale_video, args=(input_video_path, output_video_path,), daemon=True)
# print("Hi")
# p.start()
# p.join()
upscale_video(input_video_path, output_video_path)


  0%|          | 0/5 [00:00<?, ?it/s]

Processing frame 1/1646


  0%|          | 0/5 [00:00<?, ?it/s]

Processing frame 2/1646


  0%|          | 0/5 [00:00<?, ?it/s]

...

  0%|          | 0/5 [00:00<?, ?it/s]

Processing frame 453/1646


  0%|          | 0/5 [00:00<?, ?it/s]

Processing frame 454/1646


  0%|          | 0/5 [00:00<?, ?it/s]